---

# TP 4 : Méthodes de quadrature de Gauss

<b>Polytech Sorbonne, Main 3</b><br>
Analyse numérique et EDO<br>
Auteur : Fabien Vergnet

---

## Table des matières

- [Exercice 1 : Méthodes de Gauss-Legendre](#gauss-legendre)
- [Exercice 2 : Le cas d'un domaine non borné](#gauss-hermite)
- [Exercice 3 : Intégrale de fonction singulière](#gauss-tchebychev)
- [Exercice 4 : Résolution d'EDO](#EDO)
- [Exercice 5 : Formules de quadrature en 2D](#2d)

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

<a id=gauss-legendre></a>
## Exercice 1 : Méthodes de Gauss-Legendre

Dans cet exercice, nous cherchons à approcher le calcul d'une intégrale $$\displaystyle \int_a^b f(x)dx$$ avec des méthodes de quadratures de Gauss-Legendre composées. Nous nous intéresserons en particulier à l'approximation des intégrales du TP précédent

$$
\displaystyle \int_{1/2}^2 \left( 1 + \dfrac{1}{x^2} \right) \arctan(x) dx = \dfrac{3\pi}{4} \quad \text{et} \quad
\int_0^{\pi/2} \dfrac{1}{1+\sin(x)} dx = 1,
$$
dont on connait les valeurs exactes.

### Question 1

Définir la fonction `GaussLegendre2` qui prend en arguments une fonction $f$, les bornes $a$ et $b$ de l'intervalle d'intégration et un entier $N$ et qui retourne une valeur approchée de l'integrale $$\int_a^b f(x)dx$$ en utilisant la méthode de Gauss-Legendre à 2 points. On définira une subdivision de l'intervalle $[a,b]$ en $N$ intervalles afin d'implémenter une méthode de quadrature composée.

In [ ]:
def f1(x):
    return (1+1./x**2)*np.arctan(x)

def f2(x):
    return 1./(1+np.sin(x))

def GaussLegendre2(f,a,b,N):
    # Compléter ici
    
### TEST
# Compléter ici

### Question 2

Pour chaque fonction `f1` et `f2`, tracer en échelle logarithmique l'erreur de quadrature obtenue en approchant l'intégrale par la formule de Gauss-Legendre à 2 points implémentée ci-dessus en fonction du nombre de sous-intervalles $N$. Justifier le comportement observé.

In [ ]:
# Compléter ici

### Question 3

Sur le graphique précédent, ajouter l'erreur de quadrature de la méthode de Simpson pour chacune des fonctions étudiées, afin de comparer les deux méthodes. Qu'observez-vous ?

### Question 4

Définir la fonction `GaussLegendre3` qui prend en arguments une fonction $f$, les bornes $a$ et $b$ de l'intervalle d'intégration et un entier $N$ et qui retourne une valeur approchée de l'integrale $$\int_a^b f(x)dx$$ en utilisant les méthodes de Gauss-Legendre à 3 points. On définira une subdivision de l'intervalle $[a,b]$ en $N$ intervalles afin d'implémenter une méthode de quadrature composée.

In [ ]:
def GaussLegendre3(f,a,b,N):
    # Compléter ici
    
### TEST
# Compléter ici

### Question 5

Pour chaque fonction `f1` et `f2`, tracer en échelle logarithmique l'erreur de quadrature obtenue en approchant l'intégrale par la formule de Gauss-Legendre à 3 points implémentée ci-dessus, en fonction du nombre de sous-intervalles $N$. Justifier le comportement observé.


In [ ]:
# Compléter ici

In [ ]:
def gauss_quadrature_3_points(f, a, b, N):
    # Les points d'abscisse et les poids pour la quadrature de Gauss à 3 points
    points = np.array([-np.sqrt(3/5), 0, np.sqrt(3/5)])  # Les abscisses des points de Gauss
    weights = np.array([5/9, 8/9, 5/9])  # Les poids associés aux points de Gauss

    # Longueur de chaque sous-intervalle
    h = (b - a) / N

    integral = 0.0
    for i in range(N):
        # Déterminer les bornes du sous-intervalle [x_i, x_{i+1}]
        x_i = a + i * h
        x_i1 = x_i + h
        
        # Transformation de l'intervalle [x_i, x_{i+1}] en [-1, 1]
        half_length = (x_i1 - x_i) / 2
        midpoint = (x_i + x_i1) / 2

        # Calcul de l'intégrale pour ce sous-intervalle
        for j in range(3):
            x_j = midpoint + half_length * points[j]
            integral += weights[j] * f(x_j)

        # Multiplier par la demi-longueur de l'intervalle pour obtenir la contribution du sous-intervalle
        integral *= half_length

    return integral

N = np.arange(10,2000,20)
E1 = np.zeros(N.size)
E2 = np.zeros(N.size)
for i in range(N.size):
    I1 = gauss_quadrature_3_points(f1,.5,2,N[i])
    I2 = gauss_quadrature_3_points(f2,0,np.pi/2.,N[i])
    E1[i] = np.abs(I1-3.*np.pi/4.)
    E2[i] = np.abs(I2-1.)

plt.figure(figsize=[10,8])
plt.title("Erreur de quadrature de la méthode de Gauss-Legendre à 3 points")
plt.xlabel(r"$N$")
plt.ylabel(r"$E(f)$")
plt.loglog(N,E1, label=r"$|I_G(f_1) - \dfrac{3\pi}{4}|$")
plt.loglog(N,E2,label=r"$|I_G(f_2) - 1|$")
plt.loglog(N,1./N**6,"--", label=r"$N \mapsto 1/N^6$")
plt.legend()
plt.plot()
plt.show()

<a id="gauss-hermite"></a>
## Exercice 2 : Le cas d'un domaine non borné

Le but de cet exercice est de mettre en place une méthode de Gauss pour l'intégrale

$$
    \int_{-\infty}^{+\infty} \cos(x) e^{-x^2}dx.
$$

Nous introduisons alors la fonction poids $\omega(x) = e^{-x^2}$, ainsi que le produit scalaire

\begin{equation*}
    \langle f,g \rangle_{\omega} = \int_{-\infty}^{+\infty} f(x)g(x) e^{-x^2} dx.
\end{equation*}

### Question 1

Définir la fonction `g` qui code pour la fonction $g(x)= \cos(x) \exp(-x^2)$ et tracer le graphe de $g$ sur l'intervalle $[-5,5]$.


In [ ]:
def g(x):
    # Compléter ici
    
# Graphe de g
# Compléter ici

### Question 2

Avec une méthode de type Newton-Cotes, on ne peux pas intégrer sur un intervalle non borné. On considère alors que la fonction $g$ décroit assez rapidement vers 0 en $-\infty$ et en $+\infty$ pour pouvoir approcher l'intégrale

$$
    \int_{-\infty}^{+\infty} \cos(x) e^{-x^2}dx.
$$

par l'intégrale

$$
    \int_{-5}^{5} \cos(x) e^{-x^2}dx.
$$

Tracer l'erreur de quadrature obtenue avec la méthode de Simpson composée sur l'intervalle [-5,5], en fonction du nombre $N$ de sous-intervalles. On prendra $N\in\{1,\dots,11\}$

**Remarque :** la valeur exacte de l'intégrale est $\dfrac{\sqrt{\pi}}{~^4\sqrt{e}} \approx 1.38$.

In [ ]:
# Compléter ici

### Question 3 


Déterminer les polynômes unitaires orthogonaux de degrés 0, 1 et 2 pour ce produit scalaire.

### RÉPONDRE ICI OU SUR FEUILLE

### Question 4

Déterminer une formule de quadrature de Gauss simple à partir des racines du polynôme de degré 2 obtenu à la question précédente. Il s'agit de la formule de quadrature de Gauss-Hermite à 2 points.

### RÉPONDRE ICI OU SUR FEUILLE

### Question 5

Implémenter cette méthode de quadrature simple et donner une valeur approchée de

\begin{equation*}
    \int_{-\infty}^{+\infty} \cos(x) e^{-x^2}dx.
\end{equation*}

Comparer avec la méthode de Simpson composée.

In [ ]:
# Compléter ici

<a id=gauss-tchebychev></a>
## Exercice 3 : Intégrale de fonction singulière

Dans cet exercice, on cherche à calculer une valeur approchée de l'intégrale 

$$ \int_{-1}^1 \dfrac{1+\cos(x)^2}{\sqrt{1-x^2}}dx. $$


### Question 1
Implémenter une méthode de quadrature de Gauss simple d'ordre 5 pour approcher cette intégrale.

### RÉPONDRE ICI OU SUR FEUILLE

In [ ]:
def GaussTchebychev3(f,a,b):
    # Compléter ici

### TEST
# Compléter ici

### Question 2

Calculer l'erreur de quadrature de cette méthode, pour le calcul de l'intégrale 

$$ \int_{-1}^1 \dfrac{1}{\sqrt{1-x^2}}dx, $$

dont on connaît une valeur exacte et comparer avec la méthode de Gauss-Legendre simple à 2 points.

In [ ]:
# Compléter ici

### Question 3

Déterminer une valeur approchée pour l'intégrale de l'énoncé.

In [ ]:
# Compléter ici

<a id=EDO></a>
## Exercice 4 : Résolution d'EDO

Dans cet exercice, on s'intéresse à la résolution d'une équation différentielle ordinaire. En particulier, on cherche une fonction $u : [a,b]\subset\mathbb{R} \mapsto \mathbb{R}$, solution de

$$
    u^\prime(t) = \gamma(t)u(t),\\
    u(a) = u_0,
$$

où $\gamma : [a,b] \times \mapsto \mathbb{R}$ est continue sur $[a,b]$ et $u_0 \in \mathbb{R}$ est la condition initiale.

### Question 1

Soit $x\in[a,b]$. Intégrer l'EDO entre $a$ et $x$ et en déduire une équation (intégrale) vérifiée par $u(x)$.

### RÉPONDRE ICI OU SUR FEUILLE

### Question 2

On considère une subdivision régulière $([x_i-1,x_{i}])_{1\leq i \leq n}$ de $[a,b]$ en $n$ sous-intervalles tels que $x_0=a < x_1 < \dots < x_{n}=b$ et de pas $h$.On cherche alors une approximation de la solution de l'EDO aux points $x_i$, i.e. une approximation de $u(x_i)$.

Pour $i\in\{0,\dots,n\}$, on note $$u_i = u(x_i).$$

À partir de la question précédente et en utilisant la formule de quadrature des rectangles à gauche, déterminer, pour tout $i\geq$, l'expression de $u_i$ en fonction de $u_{i-1}$.

***Remarque***

Cette relation entre $u_i$ et $u_{i-1}$ est ce qu'on appelle un *schéma numérique* pour les EDO. ce schéma en particulier est appellé *schéma d'Euler explicite*. En choisissant une autre formule de quadrature, on obtient un autre schéma numérique.

### RÉPONDRE ICI OU SUR FEUILLE

### Question 3

Implémenter le schéma numérique obtenu dans la fonction `schemaEDO1` ci-dessous et résoudre l'équation sur $[0,1]$, en prenant $\gamma(t) = 5$ et $u_0 = 3$

**Remarque**
La fonction devra retourner un tableau numpy $x$ contenant les points de discrétisation de l'intervalle $[a,b]$ et un tableau numpy $u$ contenant les approximation $(u_i)$.

In [ ]:
def schemaEDO(gamma,a,b,N,u0):
    # Compléter ici
    return x,u
    

# TEST
# Compléter ici

### Question 4

Déterminer la solution exacte de cette EDO et calculer l'erreur de la solution approchée en norme infinie sur l'intervalle $[0,1]$ en fonction du nombre $n$ de sous-intervalles considérés. On tracera ce graphique en échelle logarithmique.

Avez-vous une idée de l'ordre de convergence de cette méthode, i.e. du comportement de la courbe de l'erreur en fonction du pas de dicrétisation ?

In [ ]:
# Compléter ici

### Question 5

Déterminer et implémenter des schémas numériques en utilisant la formule de quadrature des rectangles à droite et la formule des points milieux.

In [ ]:
# Compléter ici

<a id=2d></a>
## Exercice 5 : Formules de quadrature en 2D

### Question 1

Déterminer une formule de quadrature pour une fonction en deux dimensions $f(x,y)$, qui utilise de l'interpolation polynomiale de degré 0, puis de de degré 1.

Réponse : à vous de bosser !

### Question 2

Définir une méthode de Gauss en deux dimensions.